# Interpolação Lagrangeana Baricêntrica
## Nelson Kuhl - IME/USP (nmkuhl@usp.br)

(Algoritmos para interpolação lagrangeana baricêntrica, conforme descrito em Berrut & Trfethen, *Barycentric Lagrange Interpolation*, SIAM Review 46(3) (2004), pp. 501--517)


Considere a tabela
$$
    \begin{array}{c|cccc}
        x & x_0 & x_1 & \dots & x_n \\
        \hline
        y & y_0 & y_1 & \dots & y_n
    \end{array} ,
$$

com $x_i \ne x_j$ se $i \ne j$.
Então, o polinômio interpolador $p_n$ da tabela na forma de Lagrange é dado por

$$
    p_n(x) = \sum_{j=0}^n y_j L_j(x)
$$

onde os polinômios de Lagrange $L_j$ são definidos por

$$
    L_j(x) = \prod^n_{\substack{k = 0 \\ k \ne j}} \frac{x - x_k}{x_j - x_k}, \quad 0 \le j \le n.
$$

Manipulando-se as fórmulas acima podemos escrever a fórmula de Lagrange modificada

$$
    p_n(x) = L(x) \sum_{j=0}^n \frac{\omega_j}{x - x_j}y_j, \quad x \ne x_i,\ 0 \le i \le n,
$$

onde

$$
L(x) = (x - x_0)(x - x_1) \dots (x - x_n)
$$

e os **pesos baricêntricos** $\omega_j$ são definidos como

$$
    \omega_j = \Bigg[\prod^n_{\substack{k=0 \\ k \ne j}}(x_j - x_k)\Bigg]^{-1}, \quad 0 \le j \le n .
$$

Sabendo-se que se $y_i = 1$, $0 \le i \le n$, então $p_n(x) = 1$, $\forall x \in \mathbb{R}$, obtemos

$$
    1 = L(x)\sum_{j=0}^n \frac{\omega_j}{x - x_j}, \quad \forall x \ne x_i,\ 0 \le i \le n,
$$

o que nos dá a **fórmula baricêntrica**

$$
    p_n(x) = \frac{\sum_{j=0}^n\frac{\omega_j}{x - x_j}y_j}{\sum_{m=0}^n\frac{\omega_m}{x - x_m}},
    \quad x \ne x_i,\ 0 \le i \le n.
$$

Há casos específicos nos quais os pesos são conhecidos explicitamente. Entre eles:

> **1)** Pontos igualmente espaçados no intervalo $[a,b]$
\begin{align}
    x_i &= a + i\cdot\left(\frac{b-a}{n}\right), \quad 0 \le i \le n,\\
    \omega_j &= (-1)^j \cdot \binom{n}{j}, \quad 0 \le j \le n.
\end{align}

> **2)** Pontos de Chebyshev do segundo tipo no intervalo $[a, b]$:
\begin{align}
    x_i &= -\frac{b-a}{2} \cdot \cos\left(\frac{i\pi}{n}\right),\quad 0 \le i \le n,\\
    \omega_j &= (-1)^j \cdot d_j,\ 0 \le j \le n, \text{ com } d_0 = d_n = 0.5,\ d_j = 1,\ 1 \le j \le n-1.
\end{align}

Note que nos dois casos os pesos independem do intervalo $[a,b]$. A diferença em cada intervalo seria um fator de escala comum a todos os pesos, o que não muda o resultado da fórmula baricêntrica.



In [ ]:
import numpy as np, matplotlib.pyplot as plt # o mínimo
from scipy.special import binom # para coeficientes binomiais
from numpy.linalg import norm as npnorm # para calcular normas

In [ ]:
# Cálculo dos pesos da fórmula baricêntrica
def weight_bary(xdata):
    # Cálculo dos pesos para a interpolação Lagrangeana baricêntrica.
    # Há duas rotinas separadas para os casos de pontos igualmente
    # espaçados e pontos de Chebyshev de segunda espécies. Ambos dependem
    # apenas da quantidade de pontos.
    
    np1 = np.size(xdata) # n + 1
        
    # espaçamento arbitrário; use a fórmula
    v = np.empty(np1)
    for j in range(np1):
        aux = xdata[j] - xdata
        mask = (aux != 0.)
        v[j] = np.prod(aux[mask])
    return 1.0/v

def weight_equi(npoints): # npoints pontos equidistantes (npoints = n+1)
    vrange = np.arange(npoints) # [0, 1, ..., n]
    return np.power(-1, vrange) * binom(npoints-1, vrange) # (-1)^j * binom(n,j), j de 0 a n

def weight_cheby2(npoints): # np pontos de Chebyshev do segundo tipo
    vrange = np.arange(npoints) # [0, 1, ..., n]
    d = np.ones(npoints - 2); d = np.insert(d, 0, 0.5); d = np.append(d, 0.5) # [0.5,1,...,1,0.5]
    return np.power(-1, vrange) * d # [0.5,-1,...,(-1)^(n-1),(-1)^n * 0.5]

In [ ]:
def eval_bary(x, xdata, ydata, w):
    # Cálculo do valor no ponto x do polinômio interpolador
    # da tabela (xdata, ydata) usando a fórmula baricêntrica,
    # onde os pesos w relativos aos pontos xdata foram
    # previamente calculados.
    #
    # OBSERVAÇÔES: 1) x pode ser escalar ou vetor
    #
    #              2) no código abaixo, pode ocorrer divisão por zero gerando resultados
    #                 do tipo inf e nan. Isso gera warnings, mas o programa executa. Esses
    #                 resultados são eliminados no final do próprio código.
    
    np1 = np.size(xdata) # n + 1
    nx = np.size(x) # funciona para escalares
    numer = np.zeros(nx); denom = np.zeros(nx)
    ind0 = np.empty(0, dtype=int); pos0 = np.empty(0, dtype=int) # Caso x coincida com pontos da tabela
    for j in range(np1):
        xdiff = x - xdata[j]
        tmp = w[j] / xdiff # eventuais divisões por zero, resultando em inf, serão eliminadas abaixo
        numer += tmp * ydata[j] # eventuais nan serão eliminados abaixo
        denom += tmp            # idem
        i0 = np.where(xdiff == 0)[0] # Verifica se há um ponto da tabela em x. O resultado de np.where
                                     # é uma tupla, cuja primeira componente é um array.
        if (np.size(i0) != 0):
            ind0 = np.append(ind0, j) # Posição em xdata
            pos0 = np.append(pos0, i0[0]) # Posição em x
    y = numer / denom
    if (np.size(ind0) != 0): # Caso haja pontos da tabela em x
        y[pos0] = ydata[ind0] # Aqui, eventuais inf e nan são substituidos pelos pontos da tabela
    if (nx > 1):
        return y # retorna um array
    else:
        return y[0] # retorna um escalar

In [ ]:
# Suprima os warnings irritantes. Comente a linha abaixo para ver o que acontece
np.seterr(divide='ignore', invalid='ignore')

### Exemplo
Considere a tabela

$$
    \begin{array}{c|rccc}
        x & -1 & 0 & 1 & 2 \\
        \hline
        2^x & 0.5 & 1 & 2 & 4
    \end{array}
$$

da função $2^x$ nos pontos $-1, 0, 1$ e $2$. Primeiramente, calculemos os pesos baricêntricos. Podemos usar a expressão para pontos igualmente espaçados:


In [ ]:
xd = np.arange(-1., 3.)
yd = np.power(2, xd)
w = weight_equi(np.size(xd))
print(w)

Que valores obteríamos se usássemos a fórmula para espaçamento arbitrário?


In [ ]:
w_arb = weight_bary(xd)
print(w_arb)

Note que o resultado é $-1/6$ vezes o resultado obtido usando a expressão para pontos igualmente espaçados. Calculemos uma aproximação para $\sqrt{2}$ usando a fórmula baricêntrica, com as duas expressões para os pesos:


In [ ]:
r2_equi = eval_bary(0.5, xd, yd, w); r2_arb = eval_bary(0.5, xd, yd, w_arb)
print("r2_equi= ", r2_equi)
print("r2_arb= ", r2_arb)

O resultado é o mesmo (módulo arredondamento). Vejamos o gráfico do polinômio interpolador, juntamente com os dados (usando os pesos da expressão para pontos igualmente espaçados) e o gráfico da função:


In [ ]:
xx = np.linspace(-1, 2, 3073) # para gerar o gráfico do polinômio interpolador, calcularemos o seu valor em pontos
                              # com espaçamento 2^(-10) no intervalo [-1, 2].
yy = eval_bary(xx, xd, yd, w)
plt.plot(xx, np.power(2, xx), label="2^x")
plt.scatter(xd, yd, label="dados")
plt.plot(xx, yy, label="pol. interp.")
plt.legend();

A aproximação parece razoável em todo o intervalo (nem sempre é assim). Para termos uma ideia da qualidade da aproximação, calculemos o erro máximo entre o polinômio interpolador e a função nos pontos usados para gerar o gráfico.


In [ ]:
print("erro máximo: {:.4f}".format(npnorm(yy - np.power(2, xx), np.inf)))

O polinômio interpolador não depende da ordem dos pontos $(x_i, y_i)$, $0 \le i \le n$. Calculemos então os pesos para a tabela dada na forma

$$
    \begin{array}{c|rccc}
        x & 1 & -1 & 2 & 0 \\
        \hline
        2^x & 2 & 0.5 & 4 & 1
    \end{array}
$$

e comparemos o valor obtido para o polinômio nos pontos usados para gerar o gráfico com os valores anteriores.


In [ ]:
xdd = np.array([1., -1., 2., 0.])
ydd = np.power(2., xdd)
print("x= ", xdd)
print("y= ", ydd)

In [ ]:
ww = weight_bary(xdd) # Temos de usar espaçamento arbitrário
print("pesos= ", ww)

In [ ]:
yy_novo = eval_bary(xx, xdd, ydd, ww)


Os resultados, dentro da precisão, são os mesmos?


In [ ]:
erro_rel = npnorm((yy_novo-yy)/yy, np.inf)
print("erro relativo máximo: {:.1e}".format(erro_rel))

### Exemplo de Runge

O exemplo de Runge é um exemplo clássico para ilustrar a não convergência do polinômio interpolador para a função quando aumentamos a quantidade de *pontos igualmente espaçados*. A função e o intervalo escolhido são:

$$
    f(x) = \frac{1}{1 + x^2},\quad x \in [-5, 5].
$$

Iremos observar o comportamento do polinômio interpolador para alguns conjuntos de pontos igualmente espaçados no intervalo $[-5,5]$.


In [ ]:
def f(x): return 1.0/(1.0 + x*x) # Função
xx = np.linspace(-5.0, 5.0, 10241) # Pontos para gerar gráficos
ff = f(xx) # Valor da função nesses pontos

In [ ]:
# EXEMPLO DE RUNGE, 3 PONTOS IGUALMENTE ESPAÇADOS
np1 = 3 # n + 1
xdata = np.linspace(-5, 5, np1)
ydata = f(xdata)
w = weight_equi(np1)
yy = eval_bary(xx, xdata, ydata, w)
plt.plot(xx, ff, label="f(x)")
plt.scatter(xdata, ydata, label="tabela")
plt.plot(xx, yy, label="pol. interp. n =2")
plt.legend(bbox_to_anchor=(1.04, 1), loc="upper left");

In [ ]:
# EXEMPLO DE RUNGE, 5 PONTOS IGUALMENTE ESPAÇADOS
np1 = 5 # n + 1
xdata = np.linspace(-5, 5, np1)
ydata = f(xdata)
w = weight_equi(np1)
yy = eval_bary(xx, xdata, ydata, w)
plt.plot(xx, ff, label="f(x)")
plt.scatter(xdata, ydata, label="tabela")
plt.plot(xx, yy, label="pol. interp. n =4")
plt.legend(bbox_to_anchor=(1.04, 1), loc="upper left");

In [ ]:
# EXEMPLO DE RUNGE, 7 PONTOS IGUALMENTE ESPAÇADOS
np1 = 7 # n + 1
xdata = np.linspace(-5, 5, np1)
ydata = f(xdata)
w = weight_equi(np1)
yy = eval_bary(xx, xdata, ydata, w)
plt.plot(xx, ff, label="f(x)")
plt.scatter(xdata, ydata, label="tabela")
plt.plot(xx, yy, label="pol. interp. n =6")
plt.legend(bbox_to_anchor=(1.04, 1), loc="upper left");

In [ ]:
# EXEMPLO DE RUNGE, 9 PONTOS IGUALMENTE ESPAÇADOS
np1 = 9 # n + 1
xdata = np.linspace(-5, 5, np1)
ydata = f(xdata)
w = weight_equi(np1)
yy = eval_bary(xx, xdata, ydata, w)
plt.plot(xx, ff, label="f(x)")
plt.scatter(xdata, ydata, label="tabela")
plt.plot(xx, yy, label="pol. interp. n =8")
plt.legend(bbox_to_anchor=(1.04, 1), loc="upper left");

In [ ]:
# EXEMPLO DE RUNGE, 11 PONTOS IGUALMENTE ESPAÇADOS
np1 = 11 # n + 1
xdata = np.linspace(-5, 5, np1)
ydata = f(xdata)
w = weight_equi(np1)
yy = eval_bary(xx, xdata, ydata, w)
plt.plot(xx, ff, label="f(x)")
plt.scatter(xdata, ydata, label="tabela")
plt.plot(xx, yy, label="pol. interp. n =10")
plt.legend(bbox_to_anchor=(1.04, 1), loc="upper left");

In [ ]:
# EXEMPLO DE RUNGE, 17 PONTOS IGUALMENTE ESPAÇADOS
np1 = 17 # n + 1
xdata = np.linspace(-5, 5, np1)
ydata = f(xdata)
w = weight_equi(np1)
yy = eval_bary(xx, xdata, ydata, w)
plt.plot(xx, ff, label="f(x)")
plt.scatter(xdata, ydata, label="tabela")
plt.plot(xx, yy, label="pol. interp. n =16")
plt.legend(bbox_to_anchor=(1.04, 1), loc="upper left");

In [ ]:
# EXEMPLO DE RUNGE, 33 PONTOS IGUALMENTE ESPAÇADOS
np1 = 33 # n + 1
xdata = np.linspace(-5, 5, np1)
ydata = f(xdata)
w = weight_equi(np1)
yy = eval_bary(xx, xdata, ydata, w)
plt.plot(xx, ff, label="f(x)")
plt.scatter(xdata, ydata, label="tabela")
plt.plot(xx, yy, label="pol. interp. n =32")
plt.legend(bbox_to_anchor=(1.04, 1), loc="upper left");

Pode-se demonstrar rigorosamente que os polinômios interpoladores aproximam a função em um intervalo em torno da origem e divergem fora dele. As figuras acima dão uma ideia do que ocorre.


### Pontos de Chebyshev de segunda espécie

Quando podemos escolher os pontos para interpolação, os resultados podem ser bem melhores. Uma classe boa é dada pelos pontos de Chebyshev de segunda espécie, que são os pontos extremos do polinômio de Chebyshev de grau $n$, contidos no intevalo $[-1,1]$. Eles são calculados pela expressão

$$
    x_i = -\cos\left(\frac{i\pi}{n}\right), \quad 0 \le i \le n.
$$

Para termos uma ideia de como eles se distribuem no intervalo $[-1, 1]$, vejamos o caso $n=32$:


In [ ]:
n = 32; x_cheby = -np.cos(np.arange(n+1)*np.pi/n)
plt.scatter(x_cheby, np.zeros(n+1));

Note que os pontos são mais rarefeitos no meio e se acumulam nos extremos do intervalo. Esta propriedade ajuda em aproximações. Em um intervalo $[a, b]$ arbitrário, transportamos esses pontos usando a transformação linear afim que leva $[-1,1]$ em $[a, b]$:

$$
    x_i = -0.5\cdot(b-a)\cdot\cos\left(\frac{i\pi}{n}\right) + 0.5\cdot(a+b), \quad 0 \le i \le n.
$$

Como ficam as aproximações para a função do exemplo de Runge usando estes pontos no intervalo $[-5,5]$?


In [ ]:
PI = np.pi

# n=2 e n=4
n = 2; xd1 = -5*np.cos(np.arange(n+1)*PI/n); yd1 = f(xd1)
w = weight_cheby2(n+1); yy1 = eval_bary(xx, xd1, yd1, w)

n = 4; xd2 = -5*np.cos(np.arange(n+1)*PI/n); yd2 = f(xd2)
w = weight_cheby2(n+1); yy2 = eval_bary(xx, xd2, yd2, w)

fig, (ax1, ax2) = plt.subplots(1,2, figsize=(20,5))
ax1.plot(xx, ff, label="f(x)"); ax1.scatter(xd1, yd1, label="tabela"); ax1.plot(xx, yy1, label="pol. interp. n=2")
ax2.plot(xx, ff, label="f(x)"); ax2.scatter(xd2, yd2, label="tabela"); ax2.plot(xx, yy2, label="pol. interp. n=4")
ax1.legend(loc='upper right'); ax2.legend(loc='upper right');

In [ ]:
# n=8 e n=16
n = 8; xd1 = -5*np.cos(np.arange(n+1)*PI/n); yd1 = f(xd1)
w = weight_cheby2(n+1); yy1 = eval_bary(xx, xd1, yd1, w)

n = 16; xd2 = -5*np.cos(np.arange(n+1)*PI/n); yd2 = f(xd2)
w = weight_cheby2(n+1); yy2 = eval_bary(xx, xd2, yd2, w)

fig, (ax1, ax2) = plt.subplots(1,2, figsize=(20,5))
ax1.plot(xx, ff, label="f(x)"); ax1.scatter(xd1, yd1, label="tabela"); ax1.plot(xx, yy1, label="pol. interp. n=8")
ax2.plot(xx, ff, label="f(x)"); ax2.scatter(xd2, yd2, label="tabela"); ax2.plot(xx, yy2, label="pol. interp. n=16")
ax1.legend(loc='upper right'); ax2.legend(loc='upper right');

In [ ]:
# n=32 e n=64
n = 32; xd1 = -5*np.cos(np.arange(n+1)*PI/n); yd1 = f(xd1)
w = weight_cheby2(n+1); yy1 = eval_bary(xx, xd1, yd1, w)

n = 64; xd2 = -5*np.cos(np.arange(n+1)*PI/n); yd2 = f(xd2)
w = weight_cheby2(n+1); yy2 = eval_bary(xx, xd2, yd2, w)

fig, (ax1, ax2) = plt.subplots(1,2, figsize=(20,5))
ax1.plot(xx, ff, label="f(x)"); ax1.scatter(xd1, yd1, label="tabela"); ax1.plot(xx, yy1, label="pol. interp. n=32")
ax2.plot(xx, ff, label="f(x)"); ax2.scatter(xd2, yd2, label="tabela"); ax2.plot(xx, yy2, label="pol. interp. n=64")
ax1.legend(loc='upper right'); ax2.legend(loc='upper right');

Cálculo do erro máximo entre o polinômio interpolador e a função nos pontos usados para gerar os gráficos,
com $n=32$ e $n=64$:

In [ ]:
err_32 = npnorm(yy1 - ff, np.inf); err_64 = npnorm(yy2 - ff, np.inf)
print("erro máximo para n=32: {:.1e}".format(err_32))
print("erro máximo para n=64: {:.1e}".format(err_64))

Parece que o erro está dimunuindo. De fato,


In [ ]:
n = 4
for k in range(6):
    n = 2*n
    xd = -5*np.cos(np.arange(n+1)*PI/n); yd = f(xd)
    w = weight_cheby2(n+1); yy = eval_bary(xx, xd, yd, w)
    err_max = npnorm(yy - ff, np.inf)
    print("erro máximo para n ={:4d}: {:8.1e}".format(n, err_max))

A convergência pode ser demonstrada rigorosamente. Vejamos um gráfico do ero (em escala logaritmica) com funçao do número de pontos.

In [ ]:
x = np.array([8, 16,32, 64, 128])                     # n
y = np.array([2e-1, 3.7e-2, 1.6e-3, 2.9e-6, 8.7e-12]) # erro
plt.scatter(x, np.log(y))
plt.xlabel("número de pontos")
plt.ylabel("log do erro");

O gráfico acima sugere que os pontos se ajustam bem a uma reta, indicando um decaimento exponencial do erro como funçao do número de pontos. Este resultado pode ser demonstrado.